In [4]:
import requests
import pandas as pd
import numpy as np
import matplotlib as plt
import tqdm
import datetime
import json
import collections
%matplotlib inline

In [5]:
sber = '3529'
page = 1
num_per_page = 100
Samara = 1

In [6]:
url = f'http://api.hh.ru/vacancies?employer_id={sber}&page={page}&per_page={num_per_page}&area={Samara}'
res = requests.get(url)
vacancies = res.json()
num_pages = vacancies.get('pages')

In [7]:
all_vacancy_ids = []
for i in tqdm.tqdm(range(num_pages)):
    url = f'http://api.hh.ru/vacancies?employer_id={sber}&page={i}&per_page={num_per_page}&area={Samara}'
    res = requests.get(url)
    vacancies = res.json()
    vacancy_ids = [el.get('id') for el in vacancies.get('items')]
    all_vacancy_ids.extend(vacancy_ids)
all_vacancy_ids

100%|██████████| 20/20 [00:08<00:00,  2.36it/s]


['46380141',
 '51731713',
 '51711228',
 '51027412',
 '51431993',
 '51648092',
 '51626043',
 '46943947',
 '51285630',
 '51407606',
 '51276841',
 '50172507',
 '50296217',
 '51694775',
 '50977075',
 '50712438',
 '51589229',
 '50928878',
 '51342385',
 '51644927',
 '50731679',
 '51362903',
 '51589255',
 '51001496',
 '51214470',
 '50579795',
 '51345153',
 '47892104',
 '51287726',
 '51431896',
 '51656253',
 '50879518',
 '51181110',
 '50710091',
 '50707523',
 '51433739',
 '49981757',
 '51053410',
 '50859520',
 '51700194',
 '47409515',
 '51251211',
 '51286634',
 '50010847',
 '50334733',
 '51737942',
 '51281296',
 '50577722',
 '51270774',
 '51631958',
 '51214494',
 '50992034',
 '51656224',
 '51273162',
 '51471424',
 '51206583',
 '51272571',
 '50930733',
 '50586554',
 '51212135',
 '51422067',
 '51503401',
 '50885347',
 '50922335',
 '50440683',
 '51626053',
 '50933457',
 '51738015',
 '50031988',
 '50941817',
 '50919636',
 '51337325',
 '50567469',
 '50928272',
 '51650198',
 '51409326',
 '48481713',

In [8]:
today = datetime.datetime.now()
previous_month = today.replace(day=1) - datetime.timedelta(days=1)

all_vacancy_ids = []
interval = 14
for i in tqdm.tqdm(range(num_pages)):
    start_date = previous_month
    interval_end = start_date + datetime.timedelta(days=interval)
    end_date = today

    while start_date <= end_date:
        url = f'http://api.hh.ru/vacancies?employer_id={sber}&page={i}&per_page={num_per_page}&area={Samara}&date_from={start_date.isoformat()}&date_to={interval_end.isoformat()}'
        res = requests.get(url)
        vacancies = res.json()

        vacancy_ids = [el.get('id') for el in vacancies.get('items')]
        all_vacancy_ids.extend(vacancy_ids)

        start_date = interval_end
        interval_end = start_date + datetime.timedelta(days=interval)

100%|██████████| 20/20 [00:10<00:00,  1.88it/s]


In [9]:
len(all_vacancy_ids)

1540

In [10]:
#Вытаскиваем все вакансии с hh.ru c запросом полной информации о вакансии по ее id
all_vacancies = []
for vacid in tqdm.tqdm(all_vacancy_ids):
    url = f"https://api.hh.ru/vacancies/{vacid}"
    res = requests.get(url)
    vacancy = res.json()
    all_vacancies.append(vacancy)

100%|██████████| 1540/1540 [03:59<00:00,  6.42it/s]


In [11]:
#Сохраняем все вакансии в файл vacancies.json
with open("vacancies.json", "w") as file:
    json.dump(all_vacancies, file)

In [12]:
#Вытаскиваем все вакансии из файла vacancies.json
all_vacancies = []
with open("vacancies.json", "r") as file:
    all_vacancies = json.load(file)

In [13]:
#Вытаскиваем все полные описания вакансий
all_vacancy_descriptions = [vac.get("description") for vac in all_vacancies]
all_vacancy_descriptions

['<p>Хочешь работать в банке, но офисная рутина не для тебя?</p> <p>Мы как раз ищем менеджера, который будет продвигать продукты и сервисы экосистемы Сбера на внешних потоках клиентов.</p> <p>Тебе точно у нас понравится, если ты:</p> <ul> <li>хочешь развивать навык продаж</li> <li>готов стать экспертом в продуктах и сервисах Сбера</li> <li>легко находишь общий язык с людьми и умеешь быстро устанавливать контакт</li> </ul> <p>Нам важно, чтобы ты с радостью вставал в будни по утрам, поэтому мы предлагаем:</p> <ul> <li>шестидневное оплачиваемое обучение перед трудоустройством .</li> <li>официальное трудоустройство с первого дня.</li> <li>гибкий график работы.</li> <li>активную работу на точках продаж на территории наших партнёров (ТЦ, кофейни, торговые площадки).</li> <li>ипотеку выгоднее на 4% для каждого сотрудника</li> <li>льготные условия кредитования</li> <li>мобильную связь, корпоративный ipad и затраты на транспорт за счет компании</li> <li>теплую базу клиентов</li> <li>ДМС с перво

In [14]:
import re
for line in all_vacancy_descriptions:
    all_vacancy_descriptions_split = re.split('[^А-Яа-я]+', line.strip())
    print(all_vacancy_descriptions_split)

['', 'Хочешь', 'работать', 'в', 'банке', 'но', 'офисная', 'рутина', 'не', 'для', 'тебя', 'Мы', 'как', 'раз', 'ищем', 'менеджера', 'который', 'будет', 'продвигать', 'продукты', 'и', 'сервисы', 'экосистемы', 'Сбера', 'на', 'внешних', 'потоках', 'клиентов', 'Тебе', 'точно', 'у', 'нас', 'понравится', 'если', 'ты', 'хочешь', 'развивать', 'навык', 'продаж', 'готов', 'стать', 'экспертом', 'в', 'продуктах', 'и', 'сервисах', 'Сбера', 'легко', 'находишь', 'общий', 'язык', 'с', 'людьми', 'и', 'умеешь', 'быстро', 'устанавливать', 'контакт', 'Нам', 'важно', 'чтобы', 'ты', 'с', 'радостью', 'вставал', 'в', 'будни', 'по', 'утрам', 'поэтому', 'мы', 'предлагаем', 'шестидневное', 'оплачиваемое', 'обучение', 'перед', 'трудоустройством', 'официальное', 'трудоустройство', 'с', 'первого', 'дня', 'гибкий', 'график', 'работы', 'активную', 'работу', 'на', 'точках', 'продаж', 'на', 'территории', 'наших', 'партн', 'ров', 'ТЦ', 'кофейни', 'торговые', 'площадки', 'ипотеку', 'выгоднее', 'на', 'для', 'каждого', 'сотр

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [15]:
n = list(filter(None, all_vacancy_descriptions_split))

In [16]:
!pip install pymorphy2

In [17]:
import pymorphy2
morph = pymorphy2.MorphAnalyzer()

In [18]:
mainland = [
    [morph.parse(word)[0].normal_form for word in line.split()]
    for line in n]
print(mainland)

[['искать'], ['разработчик'], ['с'], ['опыт'], ['практический'], ['применение'], ['и'], ['построение'], ['интеграционный'], ['взаимодействие'], ['отлично'], ['понимать'], ['концепция'], ['ооп'], ['и'], ['уметь'], ['писать'], ['чистый'], ['код'], ['мы'], ['ожидать'], ['что'], ['вы'], ['отличный'], ['знание'], ['принцип'], ['ооп'], ['уверенный'], ['знание'], ['знание'], ['и'], ['опыт'], ['использование'], ['опыт'], ['использование'], ['или'], ['опыт'], ['проектирование'], ['опыт'], ['написание'], ['тест'], ['уверенный'], ['знание'], ['понимание'], ['основа'], ['протокол'], ['и'], ['архитектура'], ['система'], ['дополнительно'], ['опыт'], ['разработка'], ['приложение'], ['в'], ['микросервисный'], ['архитектура'], ['опыт'], ['работа'], ['с'], ['опыт'], ['работа'], ['с'], ['описание'], ['проект'], ['разработка'], ['и'], ['внедрение'], ['микросервис'], ['в'], ['высоконагруженный'], ['и'], ['отказоустойчивый'], ['система'], ['для'], ['дочерний'], ['банк'], ['пао'], ['сбербанк'], ['сбербанк'],

In [19]:
#3.	Взять любой текст, описывающий опыт из резюме, и аналогично предобработать

In [20]:
file = open('/Users/Roman/Desktop/Python Alex Levchenko/Итоговый проект/Описание опыта из резюме.txt', "r")#Открываем файл
all_words = []#Список со всеми словами
line = file.readline().split()#список из слов в строчке
while line:
    all_words.extend(line)#Вставляем в список с распаковкой
    line = file.readline().split()#Заново считываем
    print(all_words)

['Организация', 'работы', 'коллегиального', 'органа,', 'технический', 'секретарь', 'Правления', 'Банка:', 'Замещающий', 'секретарь', 'Комитета', 'по', 'предоставлению', 'кредитов', 'и', 'инвестиций;', 'Комитета', 'по', 'розничному', 'кредитованию.', 'Осуществляет', 'организационно-техническое', 'обеспечение', 'заседаний', 'Правления.']
['Организация', 'работы', 'коллегиального', 'органа,', 'технический', 'секретарь', 'Правления', 'Банка:', 'Замещающий', 'секретарь', 'Комитета', 'по', 'предоставлению', 'кредитов', 'и', 'инвестиций;', 'Комитета', 'по', 'розничному', 'кредитованию.', 'Осуществляет', 'организационно-техническое', 'обеспечение', 'заседаний', 'Правления.', 'Проведение', 'заседаний,', 'формирование', 'и', 'согласование', 'повестки,', 'даты', 'и', 'времени', 'проведения', 'заседания', 'с', 'Председателем', 'Комитета,', 'Правления,', 'приглашение', 'членов', 'и', 'участников', 'на', 'заседание.', 'Оформление', 'постановлений,', 'решений', 'и', 'протоколов', 'заседаний,', 'обесп

In [21]:
new_words = [re.sub('[!#?,.:";-]', '', word) for word in all_words]

In [22]:
print(new_words)

['Организация', 'работы', 'коллегиального', 'органа', 'технический', 'секретарь', 'Правления', 'Банка', 'Замещающий', 'секретарь', 'Комитета', 'по', 'предоставлению', 'кредитов', 'и', 'инвестиций', 'Комитета', 'по', 'розничному', 'кредитованию', 'Осуществляет', 'организационнотехническое', 'обеспечение', 'заседаний', 'Правления', 'Проведение', 'заседаний', 'формирование', 'и', 'согласование', 'повестки', 'даты', 'и', 'времени', 'проведения', 'заседания', 'с', 'Председателем', 'Комитета', 'Правления', 'приглашение', 'членов', 'и', 'участников', 'на', 'заседание', 'Оформление', 'постановлений', 'решений', 'и', 'протоколов', 'заседаний', 'обеспечение', 'сохранности', 'документов', 'до', 'сдачи', 'в', 'архив', 'Регистрация', 'и', 'доведение', 'принятых', 'постановлений', 'в', 'СЭОДО', 'до', 'соответствующих', 'подразделений', 'Банка', 'Подготовка', 'материалов', 'о', 'ходе', 'выполнения', 'поручений', 'Правления', 'Справочноинформационная', 'работа', 'по', 'ранее', 'принятым', 'решениям', 

In [23]:
n_rezume = list(filter(None, new_words))

In [24]:
print(n_rezume)

['Организация', 'работы', 'коллегиального', 'органа', 'технический', 'секретарь', 'Правления', 'Банка', 'Замещающий', 'секретарь', 'Комитета', 'по', 'предоставлению', 'кредитов', 'и', 'инвестиций', 'Комитета', 'по', 'розничному', 'кредитованию', 'Осуществляет', 'организационнотехническое', 'обеспечение', 'заседаний', 'Правления', 'Проведение', 'заседаний', 'формирование', 'и', 'согласование', 'повестки', 'даты', 'и', 'времени', 'проведения', 'заседания', 'с', 'Председателем', 'Комитета', 'Правления', 'приглашение', 'членов', 'и', 'участников', 'на', 'заседание', 'Оформление', 'постановлений', 'решений', 'и', 'протоколов', 'заседаний', 'обеспечение', 'сохранности', 'документов', 'до', 'сдачи', 'в', 'архив', 'Регистрация', 'и', 'доведение', 'принятых', 'постановлений', 'в', 'СЭОДО', 'до', 'соответствующих', 'подразделений', 'Банка', 'Подготовка', 'материалов', 'о', 'ходе', 'выполнения', 'поручений', 'Правления', 'Справочноинформационная', 'работа', 'по', 'ранее', 'принятым', 'решениям', 

In [25]:
import pymorphy2
morph = pymorphy2.MorphAnalyzer()

In [26]:
island = [
    [morph.parse(word)[0].normal_form for word in line.split()]
    for line in n_rezume]
print(island)

[['организация'], ['работа'], ['коллегиальный'], ['орган'], ['технический'], ['секретарь'], ['правление'], ['банк'], ['замещать'], ['секретарь'], ['комитет'], ['по'], ['предоставление'], ['кредит'], ['и'], ['инвестиция'], ['комитет'], ['по'], ['розничный'], ['кредитование'], ['осуществлять'], ['организационнотехнический'], ['обеспечение'], ['заседание'], ['правление'], ['проведение'], ['заседание'], ['формирование'], ['и'], ['согласование'], ['повестка'], ['дата'], ['и'], ['время'], ['проведение'], ['заседание'], ['с'], ['председатель'], ['комитет'], ['правление'], ['приглашение'], ['член'], ['и'], ['участник'], ['на'], ['заседание'], ['оформление'], ['постановление'], ['решение'], ['и'], ['протокол'], ['заседание'], ['обеспечение'], ['сохранность'], ['документ'], ['до'], ['сдача'], ['в'], ['архив'], ['регистрация'], ['и'], ['доведение'], ['принять'], ['постановление'], ['в'], ['сэодый'], ['до'], ['соответствующий'], ['подразделение'], ['банк'], ['подготовка'], ['материал'], ['о'], ['х

In [27]:
for word in new_words:
    p_rezume = morph.parse(word)[0]
    print(p_rezume.normal_form)

организация
работа
коллегиальный
орган
технический
секретарь
правление
банк
замещать
секретарь
комитет
по
предоставление
кредит
и
инвестиция
комитет
по
розничный
кредитование
осуществлять
организационнотехнический
обеспечение
заседание
правление
проведение
заседание
формирование
и
согласование
повестка
дата
и
время
проведение
заседание
с
председатель
комитет
правление
приглашение
член
и
участник
на
заседание
оформление
постановление
решение
и
протокол
заседание
обеспечение
сохранность
документ
до
сдача
в
архив
регистрация
и
доведение
принять
постановление
в
сэодый
до
соответствующий
подразделение
банк
подготовка
материал
о
ход
выполнение
поручение
правление
справочноинформационный
работа
по
ранее
принять
решение
постановление
правление
консультация
внутренний
клиент
по
вопрос
оформление
регистрация
и
подготовка
документ
к
заседание
с
участие
руководство
банк
контрольноаналитический
работа
формирование
контрольный
поручение
в
сэодый
постановка
поручение
на
контроль
учёт
информация
о
ход

In [28]:
#4.	Посчитать векторное представление описаний вакансий и опыта из резюме

In [29]:
from sklearn.feature_extraction.text import TfidfVectorizer

In [30]:
#Векторное представление описаний вакансий
vect = sum(mainland, [])
vectorizer = TfidfVectorizer(min_df=1)
X = vectorizer.fit_transform(vect)
idf1 = vectorizer.idf_
d = dict(zip(vectorizer.get_feature_names(), idf1))
sorted_d = sorted(d.items())
sorted_d

[('аналитик', 5.297285406218791),
 ('архитектор', 5.297285406218791),
 ('архитектура', 4.891820298110627),
 ('аудитория', 5.297285406218791),
 ('банк', 4.891820298110627),
 ('беларусь', 5.297285406218791),
 ('взаимодействие', 5.297285406218791),
 ('внедрение', 5.297285406218791),
 ('вы', 5.297285406218791),
 ('высоконагруженный', 5.297285406218791),
 ('для', 4.604138225658845),
 ('дополнительно', 5.297285406218791),
 ('доработка', 4.891820298110627),
 ('дочерний', 4.891820298110627),
 ('единый', 5.297285406218791),
 ('есть', 5.297285406218791),
 ('заниматься', 5.297285406218791),
 ('знание', 4.380994674344636),
 ('или', 5.297285406218791),
 ('инженер', 5.297285406218791),
 ('инструмент', 5.297285406218791),
 ('интеграционный', 4.604138225658845),
 ('интерфейс', 5.297285406218791),
 ('информационный', 5.297285406218791),
 ('искать', 5.297285406218791),
 ('использование', 4.891820298110627),
 ('использовать', 5.297285406218791),
 ('казахстан', 5.297285406218791),
 ('код', 5.2972854062187

In [31]:
vect_idf1 = print(*idf1, sep=', ')

5.297285406218791, 5.297285406218791, 4.891820298110627, 5.297285406218791, 4.891820298110627, 5.297285406218791, 5.297285406218791, 5.297285406218791, 5.297285406218791, 5.297285406218791, 4.604138225658845, 5.297285406218791, 4.891820298110627, 4.891820298110627, 5.297285406218791, 5.297285406218791, 5.297285406218791, 4.380994674344636, 5.297285406218791, 5.297285406218791, 5.297285406218791, 4.604138225658845, 5.297285406218791, 5.297285406218791, 5.297285406218791, 4.891820298110627, 5.297285406218791, 5.297285406218791, 5.297285406218791, 4.891820298110627, 5.297285406218791, 5.297285406218791, 4.891820298110627, 5.297285406218791, 5.297285406218791, 5.297285406218791, 5.297285406218791, 5.297285406218791, 5.297285406218791, 4.891820298110627, 5.297285406218791, 5.297285406218791, 5.297285406218791, 5.297285406218791, 5.297285406218791, 4.891820298110627, 5.297285406218791, 5.297285406218791, 3.793208009442517, 5.297285406218791, 5.297285406218791, 5.297285406218791, 5.2972854062

In [32]:
import numpy as np
array1 = np.array(idf1)

In [33]:
print(array1)

[5.29728541 5.29728541 4.8918203  5.29728541 4.8918203  5.29728541
 5.29728541 5.29728541 5.29728541 5.29728541 4.60413823 5.29728541
 4.8918203  4.8918203  5.29728541 5.29728541 5.29728541 4.38099467
 5.29728541 5.29728541 5.29728541 4.60413823 5.29728541 5.29728541
 5.29728541 4.8918203  5.29728541 5.29728541 5.29728541 4.8918203
 5.29728541 5.29728541 4.8918203  5.29728541 5.29728541 5.29728541
 5.29728541 5.29728541 5.29728541 4.8918203  5.29728541 5.29728541
 5.29728541 5.29728541 5.29728541 4.8918203  5.29728541 5.29728541
 3.79320801 5.29728541 5.29728541 5.29728541 5.29728541 5.29728541
 5.29728541 5.29728541 5.29728541 5.29728541 5.29728541 5.29728541
 5.29728541 5.29728541 5.29728541 5.29728541 5.29728541 5.29728541
 5.29728541 5.29728541 5.29728541 5.29728541 5.29728541 5.29728541
 4.8918203  5.29728541 5.29728541 4.38099467 4.60413823 4.38099467
 5.29728541 4.38099467 5.29728541 5.29728541 5.29728541 5.29728541
 5.29728541 4.8918203  5.29728541 5.29728541 5.29728541 5.29728

In [34]:
#Векторное представление опыта из резюме
vect_rezume = sum(island, [])
vectorizer = TfidfVectorizer(min_df=1)
X_ = vectorizer.fit_transform(vect_rezume)
idf = vectorizer.idf_
d_ = dict(zip(vectorizer.get_feature_names(), idf))
sorted_d_ = sorted(d_.items())
sorted_d_

[('архив', 5.22683374526818),
 ('банк', 4.533686564708234),
 ('внутренний', 5.22683374526818),
 ('вопрос', 4.821368637160015),
 ('время', 5.22683374526818),
 ('выполнение', 5.22683374526818),
 ('дата', 5.22683374526818),
 ('до', 4.821368637160015),
 ('доведение', 5.22683374526818),
 ('документ', 4.821368637160015),
 ('замещать', 5.22683374526818),
 ('заседание', 3.9740707767728116),
 ('инвестиция', 5.22683374526818),
 ('информация', 5.22683374526818),
 ('исполнение', 4.533686564708234),
 ('исполнитель', 5.22683374526818),
 ('клиент', 5.22683374526818),
 ('коллегиальный', 5.22683374526818),
 ('комитет', 4.533686564708234),
 ('консультация', 4.821368637160015),
 ('контролировать', 5.22683374526818),
 ('контроль', 4.533686564708234),
 ('контрольноаналитический', 5.22683374526818),
 ('контрольный', 5.22683374526818),
 ('кредит', 5.22683374526818),
 ('кредитование', 5.22683374526818),
 ('материал', 5.22683374526818),
 ('на', 4.821368637160015),
 ('обеспечение', 4.821368637160015),
 ('орган'

In [35]:
vect_idf = print(*idf, sep=', ')

5.22683374526818, 4.533686564708234, 5.22683374526818, 4.821368637160015, 5.22683374526818, 5.22683374526818, 5.22683374526818, 4.821368637160015, 5.22683374526818, 4.821368637160015, 5.22683374526818, 3.9740707767728116, 5.22683374526818, 5.22683374526818, 4.533686564708234, 5.22683374526818, 5.22683374526818, 5.22683374526818, 4.533686564708234, 4.821368637160015, 5.22683374526818, 4.533686564708234, 5.22683374526818, 5.22683374526818, 5.22683374526818, 5.22683374526818, 5.22683374526818, 4.821368637160015, 4.821368637160015, 5.22683374526818, 5.22683374526818, 5.22683374526818, 5.22683374526818, 5.22683374526818, 4.821368637160015, 4.12822145660007, 5.22683374526818, 4.533686564708234, 5.22683374526818, 4.12822145660007, 5.22683374526818, 4.533686564708234, 4.12822145660007, 5.22683374526818, 5.22683374526818, 5.22683374526818, 4.821368637160015, 4.821368637160015, 5.22683374526818, 4.533686564708234, 5.22683374526818, 4.821368637160015, 4.821368637160015, 5.22683374526818, 5.226833

In [36]:
array2 = np.array(idf)

In [37]:
print(array2)

[5.22683375 4.53368656 5.22683375 4.82136864 5.22683375 5.22683375
 5.22683375 4.82136864 5.22683375 4.82136864 5.22683375 3.97407078
 5.22683375 5.22683375 4.53368656 5.22683375 5.22683375 5.22683375
 4.53368656 4.82136864 5.22683375 4.53368656 5.22683375 5.22683375
 5.22683375 5.22683375 5.22683375 4.82136864 4.82136864 5.22683375
 5.22683375 5.22683375 5.22683375 5.22683375 4.82136864 4.12822146
 5.22683375 4.53368656 5.22683375 4.12822146 5.22683375 4.53368656
 4.12822146 5.22683375 5.22683375 5.22683375 4.82136864 4.82136864
 5.22683375 4.53368656 5.22683375 4.82136864 4.82136864 5.22683375
 5.22683375 5.22683375 4.82136864 5.22683375 5.22683375 5.22683375
 5.22683375 5.22683375 5.22683375 4.82136864 5.22683375 5.22683375
 5.22683375 5.22683375 4.82136864 4.53368656 5.22683375]


In [38]:
b = [str(i) for i in sorted_d]

In [39]:
print(b)

["('аналитик', 5.297285406218791)", "('архитектор', 5.297285406218791)", "('архитектура', 4.891820298110627)", "('аудитория', 5.297285406218791)", "('банк', 4.891820298110627)", "('беларусь', 5.297285406218791)", "('взаимодействие', 5.297285406218791)", "('внедрение', 5.297285406218791)", "('вы', 5.297285406218791)", "('высоконагруженный', 5.297285406218791)", "('для', 4.604138225658845)", "('дополнительно', 5.297285406218791)", "('доработка', 4.891820298110627)", "('дочерний', 4.891820298110627)", "('единый', 5.297285406218791)", "('есть', 5.297285406218791)", "('заниматься', 5.297285406218791)", "('знание', 4.380994674344636)", "('или', 5.297285406218791)", "('инженер', 5.297285406218791)", "('инструмент', 5.297285406218791)", "('интеграционный', 4.604138225658845)", "('интерфейс', 5.297285406218791)", "('информационный', 5.297285406218791)", "('искать', 5.297285406218791)", "('использование', 4.891820298110627)", "('использовать', 5.297285406218791)", "('казахстан', 5.29728540621879

In [40]:
b_rezume = [str(i) for i in sorted_d_]

In [41]:
print(b_rezume)

["('архив', 5.22683374526818)", "('банк', 4.533686564708234)", "('внутренний', 5.22683374526818)", "('вопрос', 4.821368637160015)", "('время', 5.22683374526818)", "('выполнение', 5.22683374526818)", "('дата', 5.22683374526818)", "('до', 4.821368637160015)", "('доведение', 5.22683374526818)", "('документ', 4.821368637160015)", "('замещать', 5.22683374526818)", "('заседание', 3.9740707767728116)", "('инвестиция', 5.22683374526818)", "('информация', 5.22683374526818)", "('исполнение', 4.533686564708234)", "('исполнитель', 5.22683374526818)", "('клиент', 5.22683374526818)", "('коллегиальный', 5.22683374526818)", "('комитет', 4.533686564708234)", "('консультация', 4.821368637160015)", "('контролировать', 5.22683374526818)", "('контроль', 4.533686564708234)", "('контрольноаналитический', 5.22683374526818)", "('контрольный', 5.22683374526818)", "('кредит', 5.22683374526818)", "('кредитование', 5.22683374526818)", "('материал', 5.22683374526818)", "('на', 4.821368637160015)", "('обеспечение', 

In [42]:
import numpy as np
skill = np.reshape(array1, (-1, 1))
skill1 = np.reshape(array2, (-1, 1))

In [43]:
print(skill)

[[5.29728541]
 [5.29728541]
 [4.8918203 ]
 [5.29728541]
 [4.8918203 ]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [4.60413823]
 [5.29728541]
 [4.8918203 ]
 [4.8918203 ]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [4.38099467]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [4.60413823]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [4.8918203 ]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [4.8918203 ]
 [5.29728541]
 [5.29728541]
 [4.8918203 ]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [4.8918203 ]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [4.8918203 ]
 [5.29728541]
 [5.29728541]
 [3.79320801]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29728541]
 [5.29

In [44]:
print(skill1)

[[5.22683375]
 [4.53368656]
 [5.22683375]
 [4.82136864]
 [5.22683375]
 [5.22683375]
 [5.22683375]
 [4.82136864]
 [5.22683375]
 [4.82136864]
 [5.22683375]
 [3.97407078]
 [5.22683375]
 [5.22683375]
 [4.53368656]
 [5.22683375]
 [5.22683375]
 [5.22683375]
 [4.53368656]
 [4.82136864]
 [5.22683375]
 [4.53368656]
 [5.22683375]
 [5.22683375]
 [5.22683375]
 [5.22683375]
 [5.22683375]
 [4.82136864]
 [4.82136864]
 [5.22683375]
 [5.22683375]
 [5.22683375]
 [5.22683375]
 [5.22683375]
 [4.82136864]
 [4.12822146]
 [5.22683375]
 [4.53368656]
 [5.22683375]
 [4.12822146]
 [5.22683375]
 [4.53368656]
 [4.12822146]
 [5.22683375]
 [5.22683375]
 [5.22683375]
 [4.82136864]
 [4.82136864]
 [5.22683375]
 [4.53368656]
 [5.22683375]
 [4.82136864]
 [4.82136864]
 [5.22683375]
 [5.22683375]
 [5.22683375]
 [4.82136864]
 [5.22683375]
 [5.22683375]
 [5.22683375]
 [5.22683375]
 [5.22683375]
 [5.22683375]
 [4.82136864]
 [5.22683375]
 [5.22683375]
 [5.22683375]
 [5.22683375]
 [4.82136864]
 [4.53368656]
 [5.22683375]]


In [61]:
#дополняем нулями массив опыта работы из резюме до совпадения с описанием вакансий
import numpy as np
skill1_ = np.append(skill1, [0]*22)
print(skill1_)

[5.22683375 4.53368656 5.22683375 4.82136864 5.22683375 5.22683375
 5.22683375 4.82136864 5.22683375 4.82136864 5.22683375 3.97407078
 5.22683375 5.22683375 4.53368656 5.22683375 5.22683375 5.22683375
 4.53368656 4.82136864 5.22683375 4.53368656 5.22683375 5.22683375
 5.22683375 5.22683375 5.22683375 4.82136864 4.82136864 5.22683375
 5.22683375 5.22683375 5.22683375 5.22683375 4.82136864 4.12822146
 5.22683375 4.53368656 5.22683375 4.12822146 5.22683375 4.53368656
 4.12822146 5.22683375 5.22683375 5.22683375 4.82136864 4.82136864
 5.22683375 4.53368656 5.22683375 4.82136864 4.82136864 5.22683375
 5.22683375 5.22683375 4.82136864 5.22683375 5.22683375 5.22683375
 5.22683375 5.22683375 5.22683375 4.82136864 5.22683375 5.22683375
 5.22683375 5.22683375 4.82136864 4.53368656 5.22683375 0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.  

In [62]:
import numpy as np
skill_ = np.append(skill, [0]*0)
print(skill_)

[5.29728541 5.29728541 4.8918203  5.29728541 4.8918203  5.29728541
 5.29728541 5.29728541 5.29728541 5.29728541 4.60413823 5.29728541
 4.8918203  4.8918203  5.29728541 5.29728541 5.29728541 4.38099467
 5.29728541 5.29728541 5.29728541 4.60413823 5.29728541 5.29728541
 5.29728541 4.8918203  5.29728541 5.29728541 5.29728541 4.8918203
 5.29728541 5.29728541 4.8918203  5.29728541 5.29728541 5.29728541
 5.29728541 5.29728541 5.29728541 4.8918203  5.29728541 5.29728541
 5.29728541 5.29728541 5.29728541 4.8918203  5.29728541 5.29728541
 3.79320801 5.29728541 5.29728541 5.29728541 5.29728541 5.29728541
 5.29728541 5.29728541 5.29728541 5.29728541 5.29728541 5.29728541
 5.29728541 5.29728541 5.29728541 5.29728541 5.29728541 5.29728541
 5.29728541 5.29728541 5.29728541 5.29728541 5.29728541 5.29728541
 4.8918203  5.29728541 5.29728541 4.38099467 4.60413823 4.38099467
 5.29728541 4.38099467 5.29728541 5.29728541 5.29728541 5.29728541
 5.29728541 4.8918203  5.29728541 5.29728541 5.29728541 5.29728

In [63]:
#5.	Посчитать косинусную меру сходства для опыта и описаний вакансий

In [64]:
sk = np.reshape(skill_, (-1, 1))
ski = np.reshape(skill1_, (-1, 1))

In [65]:
from sklearn.metrics.pairwise import cosine_similarity
cosine_n = print(cosine_similarity(sk, ski))

[[1. 1. 1. ... 0. 0. 0.]
 [1. 1. 1. ... 0. 0. 0.]
 [1. 1. 1. ... 0. 0. 0.]
 ...
 [1. 1. 1. ... 0. 0. 0.]
 [1. 1. 1. ... 0. 0. 0.]
 [1. 1. 1. ... 0. 0. 0.]]


In [66]:
def cosine_sim_vectors(array1, array2):
    vec1 = array1.reshape(1, -1)
    vec2 = array2.reshape(1, -1)
    return cosine_similarity(vec1, vec2)[0][0]

In [67]:
cosine_sim_vectors(array1[1], array2[1])

1.0

In [68]:
#Скрипт с результатом косинусного сходства
from scipy import spatial
result = 1 - spatial.distance.cosine(skill, skill1_)
result

0.8737102256224024

In [69]:
#пробный вариант
similarity_scores = skill.dot(skill1_)/ (np.linalg.norm(skill, axis=1) * np.linalg.norm(skill1_))
print(similarity_scores)

ValueError: shapes (93,1) and (93,) not aligned: 1 (dim 1) != 93 (dim 0)

In [70]:
#6.	Ранжировать вакансии по мере их сходства с опытом

In [71]:
related_docs_indices = result.argsort()[:-5:-1]
related_docs_indices
result[related_docs_indices]

IndexError: invalid index to scalar variable.

In [72]:
res = []
for obj1 in island:
    obj1_unique = set(word.lower() for word in obj1 if len(word.strip()) != 0 and word != '\n')
    for obj2 in island:
        obj2_unique = set(word.lower() for word in obj2 if len(word.strip()) != 0 and word != '\n')
        common = obj1_unique & obj2_unique
        if len(common) > len(obj1_unique) * 0.4:
            res.append(obj1)
print(*res, sep = '\n')

['организация']
['работа']
['работа']
['работа']
['коллегиальный']
['орган']
['технический']
['секретарь']
['секретарь']
['правление']
['правление']
['правление']
['правление']
['правление']
['банк']
['банк']
['банк']
['замещать']
['секретарь']
['секретарь']
['комитет']
['комитет']
['комитет']
['по']
['по']
['по']
['по']
['по']
['предоставление']
['кредит']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['инвестиция']
['комитет']
['комитет']
['комитет']
['по']
['по']
['по']
['по']
['по']
['розничный']
['кредитование']
['осуществлять']
['организационнотехнический']
['обеспечение']
['обеспечение']
['заседание']
['заседание']
['заседание']
['заседание']
['заседание']
['заседание']
['правление']
['правление']
['правление']
['правление']
['правление']
['проведение']
['проведение']
['заседание']
['заседание']
['заседание']
['заседание']
['заседание']
['заседание']
['формирование']
['формирование']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['согласование']
['повестка']
['дата']
['и']
[

In [73]:
plist = list(island)
island_k = plist.remove(['и'])

In [74]:
plist_ = list(mainland)
mainland_k = plist_.remove(['и'])

In [75]:
from nltk.corpus import stopwords
russian_stopwords = stopwords.words("russian")
russian_stopwords.extend([['о'], ['по']])

In [76]:
tokens_without_sw = [word for word in island if not word in stopwords.words()]
print(tokens_without_sw)

[['организация'], ['работа'], ['коллегиальный'], ['орган'], ['технический'], ['секретарь'], ['правление'], ['банк'], ['замещать'], ['секретарь'], ['комитет'], ['по'], ['предоставление'], ['кредит'], ['и'], ['инвестиция'], ['комитет'], ['по'], ['розничный'], ['кредитование'], ['осуществлять'], ['организационнотехнический'], ['обеспечение'], ['заседание'], ['правление'], ['проведение'], ['заседание'], ['формирование'], ['и'], ['согласование'], ['повестка'], ['дата'], ['и'], ['время'], ['проведение'], ['заседание'], ['с'], ['председатель'], ['комитет'], ['правление'], ['приглашение'], ['член'], ['и'], ['участник'], ['на'], ['заседание'], ['оформление'], ['постановление'], ['решение'], ['и'], ['протокол'], ['заседание'], ['обеспечение'], ['сохранность'], ['документ'], ['до'], ['сдача'], ['в'], ['архив'], ['регистрация'], ['и'], ['доведение'], ['принять'], ['постановление'], ['в'], ['сэодый'], ['до'], ['соответствующий'], ['подразделение'], ['банк'], ['подготовка'], ['материал'], ['о'], ['х

In [77]:
tokens_without_sw_m = [word for word in mainland if not word in stopwords.words()]
print(tokens_without_sw_m)

[['искать'], ['разработчик'], ['с'], ['опыт'], ['практический'], ['применение'], ['и'], ['построение'], ['интеграционный'], ['взаимодействие'], ['отлично'], ['понимать'], ['концепция'], ['ооп'], ['и'], ['уметь'], ['писать'], ['чистый'], ['код'], ['мы'], ['ожидать'], ['что'], ['вы'], ['отличный'], ['знание'], ['принцип'], ['ооп'], ['уверенный'], ['знание'], ['знание'], ['и'], ['опыт'], ['использование'], ['опыт'], ['использование'], ['или'], ['опыт'], ['проектирование'], ['опыт'], ['написание'], ['тест'], ['уверенный'], ['знание'], ['понимание'], ['основа'], ['протокол'], ['и'], ['архитектура'], ['система'], ['дополнительно'], ['опыт'], ['разработка'], ['приложение'], ['в'], ['микросервисный'], ['архитектура'], ['опыт'], ['работа'], ['с'], ['опыт'], ['работа'], ['с'], ['описание'], ['проект'], ['разработка'], ['и'], ['внедрение'], ['микросервис'], ['в'], ['высоконагруженный'], ['и'], ['отказоустойчивый'], ['система'], ['для'], ['дочерний'], ['банк'], ['пао'], ['сбербанк'], ['сбербанк'],

In [78]:
res = []
for obj1 in tokens_without_sw:
    obj1_unique = set(word.lower() for word in obj1 if len(word.strip()) != 0 and word != '\n')
    for obj2 in tokens_without_sw_m:
        obj2_unique = set(word.lower() for word in obj2 if len(word.strip()) != 0 and word != '\n')
        common = obj1_unique & obj2_unique
        if len(common) > len(obj1_unique) * 0.4:
            res.append(obj1)
print(*res, sep = '\n')

['работа']
['работа']
['банк']
['банк']
['по']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['по']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['с']
['с']
['с']
['с']
['с']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['протокол']
['в']
['в']
['в']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['в']
['в']
['в']
['банк']
['банк']
['работа']
['работа']
['по']
['по']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['с']
['с']
['с']
['с']
['с']
['банк']
['банк']
['работа']
['работа']
['в']
['в']
['в']
['с']
['с']
['с']
['с']
['с']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['и']
['по']


In [79]:
order = skill.argsort() + skill1_.argsort()
rank = order.argsort()
print(rank)

[[92 28 64 ... 18  1  0]
 [92 28 64 ... 18  1  0]
 [92 28 64 ... 18  1  0]
 ...
 [92 28 64 ... 18  1  0]
 [92 28 64 ... 18  1  0]
 [92 28 64 ... 18  1  0]]


In [80]:
#25.01.2022
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.metrics.pairwise import cosine_similarity
cv = CountVectorizer()

In [81]:
count_matrix = cv.fit_transform(mainland)
print("Count Matrix:", count_matrix.toarray())

AttributeError: 'list' object has no attribute 'lower'

In [82]:
#7. Вывести Топ-10 наиболее релевантных

In [83]:
print(result) #косинус

0.8737102256224024


In [84]:
print(skill_) #описание вакансий

[5.29728541 5.29728541 4.8918203  5.29728541 4.8918203  5.29728541
 5.29728541 5.29728541 5.29728541 5.29728541 4.60413823 5.29728541
 4.8918203  4.8918203  5.29728541 5.29728541 5.29728541 4.38099467
 5.29728541 5.29728541 5.29728541 4.60413823 5.29728541 5.29728541
 5.29728541 4.8918203  5.29728541 5.29728541 5.29728541 4.8918203
 5.29728541 5.29728541 4.8918203  5.29728541 5.29728541 5.29728541
 5.29728541 5.29728541 5.29728541 4.8918203  5.29728541 5.29728541
 5.29728541 5.29728541 5.29728541 4.8918203  5.29728541 5.29728541
 3.79320801 5.29728541 5.29728541 5.29728541 5.29728541 5.29728541
 5.29728541 5.29728541 5.29728541 5.29728541 5.29728541 5.29728541
 5.29728541 5.29728541 5.29728541 5.29728541 5.29728541 5.29728541
 5.29728541 5.29728541 5.29728541 5.29728541 5.29728541 5.29728541
 4.8918203  5.29728541 5.29728541 4.38099467 4.60413823 4.38099467
 5.29728541 4.38099467 5.29728541 5.29728541 5.29728541 5.29728541
 5.29728541 4.8918203  5.29728541 5.29728541 5.29728541 5.29728

In [85]:
similar_vacancy = list(enumerate(cosine_n[skill1_]))
new_list = similar_vacancy
#print(new_list[0])
print(type(new_list))

TypeError: 'NoneType' object is not subscriptable

In [86]:
sorted_similar_vacancy = sorted(similar_vacancy, key=lambda x:x[1], reverse=True) #сортировка в порядке убывания

NameError: name 'similar_vacancy' is not defined

In [87]:
def get_title_from_index(index):
    return df[df.index == index]["title"].values[0]
i=0
for movie in sorted_similar_movies:
    print(get_title_from_index(movie[0]))
    i=i+1
    if i>15:
        break

NameError: name 'sorted_similar_movies' is not defined

In [88]:
related_docs_indices = result.argsort()
related_docs_indices
result[related_docs_indices]

IndexError: invalid index to scalar variable.

In [ ]:
#8.	Подготовить скрипт принимающий на вход текстовое описание опыта и выводящий Топ-10 наиболее релевантных вакансий из 100 случайно выбранных из выгрузки